In [1]:
from bs4 import BeautifulSoup
import requests
import csv
import pandas as pd
import json
import os


In [2]:
# !pip3 install selenium
# !pip install webdriver-manager

In [3]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
from selenium.common.exceptions import TimeoutException
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By

In [4]:
LOCAL_GECKO_PATH = r'/Users/meithnv/Library/Caches/Homebrew/downloads/geckodriver/0.31.0/bin/geckodriver'


In [5]:
# For Dynamic website
def loadPage(url):
    # driver = webdriver.Chrome(ChromeDriverManager().install())
    driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()))
    # driver.implicitly_wait(60)
    driver.get(url)
    page = driver.page_source
    soup = BeautifulSoup(page, "lxml")
    return soup

In [6]:
def loadInfoWithDelay(url, waitForItem, gecko_path):
    driver = webdriver.Firefox(executable_path=gecko_path)
    driver.get(url)
    timeout = 150

    try:
        element_present = EC.presence_of_element_located((By.CLASS_NAME, waitForItem))
        WebDriverWait(driver, timeout).until(element_present)
    except TimeoutException:
        print( "Timed out waiting for page to load")

    page = driver.page_source
    soup = BeautifulSoup(page, "lxml")
    return soup


In [12]:
# SINGLE PAPER DETAILS

def fetchPaperDetails(url, paperId):
    paper_det ={}
    final_pg = loadInfoWithDelay(url, 'note_content_value', LOCAL_GECKO_PATH)

    header = final_pg.find('h2', attrs={'class':'note_content_title'}).find('a').string
    pdf_link = final_pg.find('a', attrs={'class':'note_content_pdf'}).get('href')
    abstract = final_pg.find('span', attrs={'class':'note_content_value'}).string
    reviews = final_pg.findAll('div', attrs={'class':'comment-level-odd'})

    paper_reviews = []
    for r in reviews:
        # print(r)
        review ={}
        review["reviewer"] = r.find('span', attrs={'class':'signatures'}).string
        node_contents = r.findAll('div', attrs={'class':'note_contents'})
        # print(node_contents)
        for attr in node_contents:
            # print(attr)
            field = attr.find('span', attrs={'class':'note_content_field'})
            val = attr.find('span', attrs={'class':'note_content_value'})
            for f, v in zip(field ,val):
                review[str(f).split(":")[0].strip()] = v

        # print(review)
        # print('\n\n--')
        paper_reviews.append(review)
    
    # SAVE PAPER DETAILS
    paper_det['paper_id'] = paperId   
    paper_det['header'] = header 
    paper_det['abstract'] = abstract 
    paper_det['reviews'] = paper_reviews
    paper_det['url'] = pdf_link

    return paper_det

In [8]:
def savePaperJSON(obj , year, venue_type, tab_type):
    
    file_path = 'iclr/'+str(year)+'/'+venue_type+'/'+tab_type
    if not os.path.exists(file_path):
        os.makedirs(file_path)
    
    store_path = file_path+'/'+obj['paper_id']+'.json'
    
    with open(store_path, 'w') as fp:
        json.dump(obj, fp)
        fp.close()


In [9]:
# savePaperJSON(obj , 2017, 'conference', 'poster-presentations')

In [10]:
BASE_URL = 'https://openreview.net'
start_url = BASE_URL+'/group?id=ICLR.cc&referrer=%5BHomepage%5D(%2F)'
soup = loadPage(start_url)


[WDM] - Downloading: 100%|██████████| 8.04M/8.04M [00:02<00:00, 3.66MB/s]


In [13]:
year_links = soup.findAll('a', href=True)[8:12]

for l in year_links:
    year = l.get('href').split('/')[-1]
    print("YEAR "+year)
    year_link = BASE_URL+l.get('href')
   
    next_page = loadPage(year_link)

    # PAGE 2
    year_page = next_page.findAll('ul', attrs={'class': 'venues-list'})
    redirect_2 = year_page[0].findAll('a')
    # print(redirect_2)

    for rd in redirect_2: 
        print(" >"+rd.get('href'))
        venue_type = str(rd.get('href')).split('/')[-1]
        
        conference_link = BASE_URL+rd.get('href')
        print(conference_link)
        conference_pg = loadPage(conference_link)
      
        # PAGE 3 (CONFERENCES)
        tabs = conference_pg.findAll('a', href=True, attrs={'role': 'tab'})[1:]

        for tab in tabs: 
            print("  >> "+tab.get('href'))
            tab_type = str(tab.get('href')).split("#")[-1]
            link_tab = conference_link+tab.get('href')
            all_papers_pg = loadInfoWithDelay(link_tab, 'note', LOCAL_GECKO_PATH)

            # LIST OF PAPERS
            all_papers = all_papers_pg.findAll('h4')
            for paper in all_papers[1:]:
                print(" >>> PAPER : "+paper.find('a').string.strip() )
                paper_link = BASE_URL+paper.find('a').get('href')
                paperID = paper.find('a').get('href').split("=")[-1]
                print(paper_link)

                # FINAL PAPER PAGE 
                paper_details = fetchPaperDetails(paper_link, paperID)
                # print(paper_details)


                # STORE THIS IN FILE
                savePaperJSON(paper_details , year, venue_type, tab_type)
                
                
            

        

YEAR 2017
 >/group?id=ICLR.cc/2017/conference
https://openreview.net/group?id=ICLR.cc/2017/conference
  >> #poster-presentations


/var/folders/2v/8202bzhj5lbd5dyqgq4rzt7r0000gn/T/ipykernel_22863/1301047541.py:2: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Firefox(executable_path=gecko_path)


 >>> PAPER : FractalNet: Ultra-Deep Neural Networks without Residuals
https://openreview.net/forum?id=S1VaB4cex
{'paper_id': 'S1VaB4cex', 'header': 'FractalNet: Ultra-Deep Neural Networks without Residuals', 'abstract': 'We introduce a design strategy for neural network macro-architecture based on self-similarity.  Repeated application of a simple expansion rule generates deep networks whose structural layouts are precisely truncated fractals.  These networks contain interacting subpaths of different lengths, but do not include any pass-through or residual connections; every internal signal is transformed by a filter and nonlinearity before being seen by subsequent layers.  In experiments, fractal networks match the excellent performance of standard residual networks on both CIFAR and ImageNet classification tasks, thereby demonstrating that residual representations may not be fundamental to the success of extremely deep convolutional neural networks.  Rather, the key may be the abilit